# HERA SDG FRONTEND

In [1]:
from ipywidgets import interact, interactive, fixed, interact_manual, Layout, Button, Box
from IPython.display import display
import ipywidgets as widgets
import datetime
import numpy as np
! pip install -q pandas-profiling
import pandas_profiling

### 1. Create the Spark Session and Spark Context
The Spark session is the entry point into all functionality in Spark.  
You can custom your session with spark.configuration using *conf.set("spark.some.config.option", "some-value")*

In [2]:
import pandas as pd
import pyspark
from pyspark.sql import SparkSession

def createSparkContext(n_executor, memory, cpu):
    global sc
    global spark
    conf = pyspark.SparkConf()
    conf.setMaster("k8s://https://kubernetes.default.svc.cluster.local:443") # K8S is a Spark master. It creates pods with Spark workers, orchestrates those workers and returns final results to the Spark driver.
    conf.set("spark.kubernetes.container.image", "lorenzopiazza/hera_sdg:spark-py_3.1.1-python3.8") # Worker pods are created from this docker image. If you use another image, specify it instead.
    conf.set("spark.kubernetes.container.image.pullPolicy", "IfNotPresent")

    # AUTHENTICATION (required to create worker pods):
    conf.set("spark.kubernetes.authenticate.caCertFile", "/var/run/secrets/kubernetes.io/serviceaccount/ca.crt")
    conf.set("spark.kubernetes.authenticate.oauthTokenFile", "/var/run/secrets/kubernetes.io/serviceaccount/token")
    # conf.set("spark.kubernetes.authenticate.driver.serviceAccountName", "spark") # replace `my-pyspark-notebook` by the actual name of the Jupyter release

    # EXECUTORS 
    conf.set("spark.executor.memory", str(memory)+"m")
    # conf.set("spark.executor.cores", "1")
    # Oppure setta i minimi e massimi di Cpu desiderati
    conf.set("spark.kubernetes.executor.request.cores", str(cpu))
    conf.set("spark.kubernetes.executor.limit.cores", "1")
    conf.set("spark.executor.instances", n_executor) # 2 pods/workers will be created. Customize it if necessary.

    # conf.set("spark.pyspark.python", "3.7")
    # conf.set("spark.pyspark.driver.python", "/usr/bin/python3")
    # DEBUGGING
    conf.set("spark.kubernetes.executor.deleteOnTermination", "false")
    # COMMUNICATION DRIVER_EXECUTORS
    conf.set("spark.driver.host", "my-jupyter-headless-service") # this is where the DNS alias for the Spark driver come in handy. 
    conf.set("spark.driver.port", "29413") # You are free to use another number. If this port is busy, spark-shell tries to bind to another port.
    podName = ! hostname
    podName = podName[0]
    conf.set("spark.kubernetes.driver.pod.name", podName) # When this property is set, the Spark scheduler will deploy the executor pods with an OwnerReference, which in turn will ensure that once the driver pod is deleted from the cluster, all of the application’s executor pods will also be deleted
    
    # DYNAMIC ALLOCATION: scales the number of executors registered with this application up and down based on the workload.
    conf.set("spark.dynamicAllocation.enabled", "true")
    conf.set("spark.dynamicAllocation.shuffleTracking.enabled", "true")
    conf.set("spark.dynamicAllocation.initialExecutors", n_executor)
    conf.set("spark.dynamicAllocation.executorIdleTimeout", "1800s") # If an executor has been idle for more than this duration, the executor will be removed
    conf.set("spark.dynamicAllocation.cachedExecutorIdleTimeout", "3600s") # If an executor which has cached data blocks has been idle for more than this duration, the executor will be removed
    conf.set("spark.dynamicAllocation.minExecutors", 1)
    conf.set("spark.dynamicAllocation.maxExecutors", 2)
    
    spark = SparkSession \
        .builder \
        .appName("Preprocessor") \
        .config(conf = conf) \
        .getOrCreate()

    # Create a context from the specified session
    sc = spark.sparkContext.getOrCreate()
    display(sc)

In [3]:
nExec_slider  = widgets.IntSlider(min=1, max=10, step=1)
memory_Slider = widgets.IntSlider(min=512, max=4096, step=128)
cpu_slider    = widgets.FloatSlider(min=0.5, max=1, step=0.1)
sli = interact_manual(createSparkContext, n_executor = nExec_slider, memory = memory_Slider, cpu = cpu_slider)
sli.widget.children[3].description = "Create Spark context (and deploy executors)"
sli.widget.children[3].button_style = 'danger'

interactive(children=(IntSlider(value=1, description='n_executor', max=10, min=1), IntSlider(value=512, descri…

### 2. Load data from HDFS

##### Lettura di comportamenti e premi filtrando per periodo (utenti si leggono sempre tutti)

In [4]:
def validate_date(start_date):
    if(pd.to_datetime('2021-03-29') <= start_date < datetime.date.today()):
        return True
    else:
        return False

def printSepLine():
    print("============================================================================================")
    
def loadUtenti():
    global utenti_df
    utenti_df = spark.read.json("hdfs://my-hdfs-namenodes:8020/HeraSDG/raw_data/utenti/*/*/*/*/*.json")
    print("Loaded " + str(utenti_df.cache().count()) + " UTENTI")
    
def loadComportamenti(start_date):
    global comportamenti_df
    comportamenti_df = spark.read.json("hdfs://my-hdfs-namenodes:8020/HeraSDG/raw_data/comportamenti/*/*/*/*/*.json", modifiedAfter=str(start_date)+"T00:00:00")
    print("Loaded " + str(comportamenti_df.cache().count()) + " COMPORTAMENTI")
    
def loadPremi(start_date):
    global premi_df
    premi_df = spark.read.json("hdfs://my-hdfs-namenodes:8020/HeraSDG/raw_data/premi/*/*/*/*/*.json", modifiedAfter=str(start_date)+"T00:00:00")
    print("Loaded " + str(premi_df.cache().count()) + " PREMI")
    
    
def loadDataFrom(start_date):
    if (validate_date(start_date)):
        print("Loading ALL UTENTI data...")
        loadUtenti()
        printSepLine()
        print("Loading COMPORTAMENTI data FROM "+str(start_date)+"...")
        loadComportamenti(start_date)
        printSepLine()
        print("Loading PREMI datadata FROM "+str(start_date)+"...")
        loadPremi(start_date)       
    else:
        print("Choose a date between 2021-04-01 and yesterday date")

start_date_widget = widgets.DatePicker(value=pd.to_datetime('2021-04-01').date())
date_picker = interact_manual(loadDataFrom, start_date = start_date_widget)
date_picker.widget.children[1].description = "Load Data from HDFS"
date_picker.widget.children[1].button_style = "danger"

interactive(children=(DatePicker(value=datetime.date(2021, 4, 1), description='start_date'), Button(descriptio…

In [ ]:
# del utenti_df
# del comportamenti_df
# del premi_df
# del premi_camst
# del premi_conad
# del premi_hera
# del comportamenti_camst
# del comportamenti_conad
# del comportamenti_hera
# del final_data

In [5]:
# utenti_df.printSchema()
# utenti_df.describe().show()
# utenti_df.show(5)

# comportamenti_df.show(5)
# premi_df.show(5)
utenti_df.storageLevel

StorageLevel(True, True, False, True, 1)

### 3. Processing

In [6]:
############################################### Pulizia record malformati e duplicati #############################################
def cleanRecord():
    print("Pulizia Record...")
    printSepLine()
    global comportamenti_df
    global premi_df
    global utenti_df
    comportamenti_df = comportamenti_df.filter(comportamenti_df.id_utente != "").distinct() # Filtro eventuali record senza id_utente
    premi_df         = premi_df.filter(premi_df.id_utente != "")# Filtro eventuali record senza id_utente
    utenti_df        = utenti_df.filter(utenti_df.id_utente != "")


############################################### Processamento dati HERA ###############################################
def processHeraData():
    print("Processamento dati HERA...")
    printSepLine()
    ## Comportamenti HERA, raggruppati per id_utente
    global comportamenti_hera 
    comportamenti_hera = comportamenti_df.filter(comportamenti_df.Partner_erogante == "HERA") \
                                            .groupBy(comportamenti_df.id_utente) \
                                            .agg({'reward(tk)':'sum', 'Partner_erogante':'count'}) \
                                            .withColumnRenamed("count(Partner_erogante)", "num_comportamenti_HERA") \
                                            .withColumnRenamed("sum(reward(tk))", "tk_guadagnati_HERA")

    ## Premi HERA, raggruppati per id_utente
    global premi_hera
    premi_hera = premi_df.filter(premi_df.Partner_erogante == "HERA") \
                                            .groupBy(premi_df.id_utente) \
                                            .agg({'prezzo(tk)':'sum', 'Partner_erogante':'count'}) \
                                            .withColumnRenamed("count(Partner_erogante)", "num_premi_HERA") \
                                            .withColumnRenamed("sum(prezzo(tk))", "tk_spesi_HERA")

    ## Utenti che hanno fatto almeno un comportamento o acquistato almeno un premio presso HERA
    global hera_df
    hera_df = comportamenti_hera.join(premi_hera, on = "id_utente", how = "fullouter").fillna(0)



############################################### Processamento dati CONAD ###############################################
def processConadData():
    print("Processamento dati CONAD...")
    printSepLine()
    ## Comportamenti CONAD, raggruppati per id_utente
    global comportamenti_conad
    comportamenti_conad = comportamenti_df.filter(comportamenti_df.Partner_erogante == "CONAD") \
                                            .groupBy(comportamenti_df.id_utente) \
                                            .agg({'reward(tk)':'sum', 'Partner_erogante':'count'}) \
                                            .withColumnRenamed("count(Partner_erogante)", "num_comportamenti_CONAD") \
                                            .withColumnRenamed("sum(reward(tk))", "tk_guadagnati_CONAD")

    ## Premi CONAD, raggruppati per id_utente
    global premi_conad
    premi_conad = premi_df.filter(premi_df.Partner_erogante == "CONAD") \
                                            .groupBy(premi_df.id_utente) \
                                            .agg({'prezzo(tk)':'sum', 'Partner_erogante':'count'}) \
                                            .withColumnRenamed("count(Partner_erogante)", "num_premi_CONAD") \
                                            .withColumnRenamed("sum(prezzo(tk))", "tk_spesi_CONAD")

    ## Utenti che hanno fatto almeno un comportamento o acquistato almeno un premio presso CONAD
    global conad_df
    conad_df = comportamenti_conad.join(premi_conad, on = "id_utente", how = "fullouter").fillna(0)


############################################### Processamento dati HERA ###############################################
def processCamstData():
    print("Processamento dati CAMST...")
    printSepLine()
    ## Comportamenti CAMST, raggruppati per id_utente
    global comportamenti_camst
    comportamenti_camst = comportamenti_df.filter(comportamenti_df.Partner_erogante == "CAMST") \
                                            .groupBy(comportamenti_df.id_utente) \
                                            .agg({'reward(tk)':'sum', 'Partner_erogante':'count'}) \
                                            .withColumnRenamed("count(Partner_erogante)", "num_comportamenti_CAMST")\
                                            .withColumnRenamed("sum(reward(tk))", "tk_guadagnati_CAMST")

    ## Premi CAMST, raggruppati per id_utente
    global premi_camst
    premi_camst = premi_df.filter(premi_df.Partner_erogante == "CAMST") \
                                            .groupBy(premi_df.id_utente) \
                                            .agg({'prezzo(tk)':'sum', 'Partner_erogante':'count'}) \
                                            .withColumnRenamed("count(Partner_erogante)", "num_premi_CAMST") \
                                            .withColumnRenamed("sum(prezzo(tk))", "tk_spesi_CAMST")

    ## Utenti che hanno fatto almeno un comportamento o acquistato almeno un premio presso CAMST
    global camst_df
    camst_df = comportamenti_camst.join(premi_camst, on = "id_utente", how = "fullouter").fillna(0)
    


############################################### Creazione DataFrame finale ###############################################
def computePartnerFidelity(tk_guadagnati_partner, tk_spesi_partner, tk_guadagnati_tot, tk_spesi_tot):
    # The fidelity of Partner X measure how much the user interact with that partner's behaviour and reward
    # Partner_X_Fidelity (%) = (token_guadagnati_X + token_spesi_X) / (token_guadagnati_tot + token_spesi_tot)
    return (tk_guadagnati_partner + tk_spesi_partner) / (tk_guadagnati_tot + tk_spesi_tot)
    
def getFinalData():
    print("Ottenendo il DataFrame finale...")
    ## Insieme di tutti gli utenti registrati alla community, con relativi dati
    global final_data
    final_data = utenti_df.join(hera_df, on = "id_utente", how = "fullouter").fillna(0) \
                            .join(conad_df, on = "id_utente", how = "fullouter").fillna(0) \
                            .join(camst_df, on = "id_utente", how = "fullouter").fillna(0)
    
    final_data = final_data.withColumn("TOT_tk_guadagnati", final_data.tk_guadagnati_HERA + final_data.tk_guadagnati_CONAD + final_data.tk_guadagnati_CAMST) \
                            .withColumn("TOT_tk_spesi", final_data.tk_spesi_HERA + final_data.tk_spesi_CONAD + final_data.tk_spesi_CAMST)
    
    final_data = final_data.withColumn("HERA_FIDELITY(%)", computePartnerFidelity(final_data.tk_guadagnati_HERA, final_data.tk_spesi_HERA, final_data.TOT_tk_guadagnati, final_data.TOT_tk_spesi)) \
                            .withColumn("CONAD_FIDELITY(%)", computePartnerFidelity(final_data.tk_guadagnati_CONAD, final_data.tk_spesi_CONAD, final_data.TOT_tk_guadagnati, final_data.TOT_tk_spesi)) \
                            .withColumn("CAMST_FIDELITY(%)", computePartnerFidelity(final_data.tk_guadagnati_CAMST, final_data.tk_spesi_CAMST, final_data.TOT_tk_guadagnati, final_data.TOT_tk_spesi)) \
                            .drop("tk_guadagnati_HERA", "tk_spesi_HERA", "tk_guadagnati_CONAD", "tk_spesi_CONAD", "tk_guadagnati_CAMST", "tk_spesi_CAMST", "num_comportamenti_HERA" , "num_comportamenti_CONAD", "num_comportamenti_CAMST", "num_premi_HERA", "num_premi_CONAD", "num_premi_CAMST") \
                            .fillna(0)
    ## CACHING DATAFRAME IN IN-MEMORY TO SPEED UP FOLLOWING OPERATIONS
    print("The Final DataFrame has " + str(final_data.cache().count()) +" records. It has been cached for following operation.")
    
def processData():
    cleanRecord()
    processHeraData()
    processConadData()
    processCamstData()
    getFinalData()
    
processor = interact_manual(processData)
processor.widget.children[0].description = "Process Data"
processor.widget.children[0].button_style = "success"

interactive(children=(Button(description='Run Interact', style=ButtonStyle()), Output()), _dom_classes=('widge…

### 4. Visualization

In [15]:
# SHOW TOP N USER
def show_top(x, n):
    final_data.sort(x, ascending=False).show(n)
    
n_top  = widgets.IntSlider(min=1, max=10, step=1)
n_top.value = 5
ranker = interact_manual(show_top, x=["TOT_tk_guadagnati", "TOT_tk_spesi", "HERA_FIDELITY(%)", "CONAD_FIDELITY(%)", "CAMST_FIDELITY(%)"], n=n_top)
ranker.widget.children[2].description = "Show top N"
ranker.widget.children[2].button_style = "success"

interactive(children=(Dropdown(description='x', options=('TOT_tk_guadagnati', 'TOT_tk_spesi', 'HERA_FIDELITY(%…

##### Sample the Final DataFrame

In [7]:
# For visualization we use a sample of the full dataset
def sampleDataFrame(fraction):
    global sample_pandas_df
    sample_pandas_df = final_data.sample(withReplacement=False, fraction=fraction, seed=1).toPandas()

print("Actually your Final Dataset is composed by " + str(final_data.count()) + " records.")
print("Convert the PySpark DataFrame to a Pandas DataFrame to visualize it (and sample if you desire)")
fractionSlider  = widgets.FloatSlider(min=0.01, max=1.0, step=0.01)
fractioner = interact_manual(sampleDataFrame, fraction = fractionSlider)
fractioner.widget.children[1].description = "Convert and Sample DataFrame"
fractioner.widget.children[1].button_style = 'success'

Actually your Final Dataset is composed by 27444 records.
Convert the PySpark DataFrame to a Pandas DataFrame to visualize it (and sample if you desire)


interactive(children=(FloatSlider(value=0.01, description='fraction', max=1.0, min=0.01, step=0.01), Button(de…

##### Describe DataFrame

In [8]:
sample_pandas_df.profile_report()

Summarize dataset:   0%|          | 0/23 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
sample_pandas_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 258 entries, 0 to 257
Data columns (total 10 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   id_utente          258 non-null    object 
 1   Data di Nascita    258 non-null    object 
 2   Eta                258 non-null    int64  
 3   Provincia          258 non-null    object 
 4   Sesso              258 non-null    object 
 5   TOT_tk_guadagnati  258 non-null    float64
 6   TOT_tk_spesi       258 non-null    int64  
 7   HERA_FIDELITY(%)   258 non-null    float64
 8   CONAD_FIDELITY(%)  258 non-null    float64
 9   CAMST_FIDELITY(%)  258 non-null    float64
dtypes: float64(4), int64(2), object(4)
memory usage: 20.3+ KB


##### Correlation Matrix

In [ ]:
# corr = sample_pandas_df.corr()
# corr.style.background_gradient(cmap='coolwarm').set_precision(2)

##### Scatter with MatplotLib (non più necessario)

In [ ]:
import matplotlib as plt
%matplotlib widget


def scatter_plot(x, y):
    sample_pandas_df.plot(kind='scatter', x=x, y=y)
#              xTitle=x.title(), yTitle=y.title(), \
#              text='title', \
#              title=f'{y.title()} vs {x.title()}', \
#                  theme=theme, colorscale=colorscale)
  
scatter = interact(scatter_plot,
                          x=[item[0] for item in final_data.dtypes if item[1] not in ('string')], # select only the "no string" columns with a List comprehension \
                          y=[item[0] for item in final_data.dtypes if item[1] not in ('string')][1:])
#                           theme=list(cf.themes.THEMES.keys()), \
#                           colorscale=list(cf.colors._scales_names.keys()))
scatter.widget.children[2].description = "Scatter Plot Data"
scatter.widget.children[2].button_style = "success"

plt.pyplot.hist(sample_pandas_df["Eta"])

##### Scatter with Bokeh (non più necessario)

In [14]:
from bokeh.plotting import figure, show
from bokeh.models import BoxSelectTool, HoverTool, UndoTool, CrosshairTool, ColumnDataSource
# allows visualisation in notebook
from bokeh.io import output_notebook
from bokeh.resources import INLINE
output_notebook(INLINE)

def scatter_plot(x, y):
    # create a new plot with a title and axis labels
    p = figure(title="Scatter Plot", x_axis_label=x, y_axis_label=y)
    p.circle(sample_pandas_df[x], sample_pandas_df[y], legend_label="Objects", line_color="yellow", size=5, alpha=0.7)
    p.add_tools(BoxSelectTool(dimensions="width"), BoxSelectTool(dimensions="height"), CrosshairTool(),
        HoverTool(tooltips=[
            ( x, '@x' ), # use @{ } for field names with spaces
            ( y, '@y' ),
        ]))
    show(p)

scatter = interact(scatter_plot,
                          x=[item[0] for item in final_data.dtypes if item[1] not in ('string')], # select only the "no string" columns with a List comprehension \
                          y=[item[0] for item in final_data.dtypes if item[1] not in ('string')][1:])

scatter.widget.children[2].description = "Scatter Plot Data"
scatter.widget.children[2].button_style = "success"




##################################### HISTOGRAMS ################################################

# def hist_hover(column, colors=["SteelBlue", "Tan"], bins=30, log_scale=False, show_plot=True):
#     # build histogram data with Numpy
#     hist, edges = np.histogram(sample_pandas_df[column], bins = bins)
#     hist_df = pd.DataFrame({column: hist,
#                              "left": edges[:-1],
#                              "right": edges[1:]})
#     hist_df["interval"] = ["%d to %d" % (left, right) for left, 
#                            right in zip(hist_df["left"], hist_df["right"])]

#     # bokeh histogram with hover tool
#     if log_scale == True:
#         hist_df["log"] = np.log(hist_df[column])
#         src = ColumnDataSource(hist_df)
#         plot = figure(plot_height = 600, plot_width = 600,
#               title = "Histogram of {}".format(column.capitalize()),
#               x_axis_label = column.capitalize(),
#               y_axis_label = "Log Count")    
#         plot.quad(bottom = 0, top = "log",left = "left", 
#             right = "right", source = src, fill_color = colors[0], 
#             line_color = "black", fill_alpha = 0.7,
#             hover_fill_alpha = 1.0, hover_fill_color = colors[1])
#     else:
#         src = ColumnDataSource(hist_df)
#         plot = figure(plot_height = 600, plot_width = 600,
#               title = "Histogram of {}".format(column.capitalize()),
#               x_axis_label = column.capitalize(),
#               y_axis_label = "Count")    
#         plot.quad(bottom = 0, top = column,left = "left", 
#             right = "right", source = src, fill_color = colors[0], 
#             line_color = "black", fill_alpha = 0.7,
#             hover_fill_alpha = 1.0, hover_fill_color = colors[1])
#     # hover tool
#     hover = HoverTool(tooltips = [('Interval', '@interval'),
#                               ('Count', str("@" + column))])
#     plot.add_tools(hover)
#     # output
#     if show_plot == True:
#         show(plot)
#     else:
#         return plot
  

# def histotabs(dataframe, features, log_scale=False, show_plot=False):
#     hists = []
#     for f in features:
#         h = hist_hover(f, log_scale=log_scale, show_plot=show_plot)
#         p = Panel(child=h, title=f.capitalize())
#         hists.append(p)
#     t = Tabs(tabs=hists)
#     show(t)

# histotabs(sample_pandas_df, sample_pandas_df.columns)    

# def filtered_histotabs(dataframe, feature, filter_feature, log_scale=False,show_plot=False):
#     hists = []
#     for col in dataframe[filter_feature].unique():
#         sub_df = dataframe[dataframe[filter_feature] == col]
#         histo = hist_hover(sub_df, feature, log_scale=log_scale, show_plot=show_plot)
#         p = Panel(child = histo, title=col)
#         hists.append(p)
#     t = Tabs(tabs=hists)
#     show(t)
# bins_slider  = widgets.IntSlider(min=1, max=30, step=1)
# bar_plotter = interact_manual(hist_hover, column=[item[0] for item in final_data.dtypes if item[1] not in ('string')], bins = bins_slider) # select all the columns with a List comprehension

# bar_plotter.widget.children[5].description = "Bar Plot Data"
# bar_plotter.widget.children[5].button_style = "success"

# The layout() function can be used to arrange both Plots and Widgets in a grid, generating the necessary row() and column() layouts automatically.                                     
# l = layout([
#   [bollinger],
#   [sliders, plot],
#   [p1, p2, p3],
# ], sizing_mode='stretch_both')

Loading BokehJS ...

interactive(children=(Dropdown(description='x', options=('Eta', 'TOT_tk_guadagnati', 'TOT_tk_spesi', 'HERA_FID…

##### Show TOP N USER

### 5. Clustering

#### Create a features column to be used in the clustering + Standardize
Spark's implementation of KMeans is a bit different from for example scikit-learn's version. We need to store all features as an array of floats, and store this array as a column called "features". Since we do no longer need the original columns we filter them out with a select statement.

In [16]:
%%time
from pyspark.ml.clustering import KMeans
from pyspark.ml.linalg import Vectors
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler, MinMaxScaler

# a = spark.createDataFrame([(Vectors.dense([0.0, 1.0, 2.0]),), (Vectors.dense([5.0, 3.0, 3.0]),), (Vectors.dense([2.0, 5.0, 10.0]),)], ["a"])
# a.show()
# scaler = MinMaxScaler(inputCol='a', outputCol='standardized')
# data_scale = scaler.fit(a)
# data_scale.transform(a).show(truncate=False)

# Create a feature column assembling all the numeric columns in a single vector
# FEATURES_COL = [item[0] for item in final_data.dtypes if item[1] not in ('string')]
FEATURES_COL = ['Eta', 'TOT_tk_guadagnati', 'TOT_tk_spesi']

vecAssembler = VectorAssembler(
    inputCols = FEATURES_COL,
    outputCol = "features")

assembled_data = vecAssembler.transform(final_data)

# Standardize the feature column
scaler = StandardScaler(inputCol='features', outputCol='standardized')
data_scale = scaler.fit(assembled_data)

df_kmeans = data_scale.transform(assembled_data).select('id_utente', 'standardized')
df_kmeans.cache().count()
df_kmeans.show(10, truncate=False)


+---------+----------------------------------------------------------+
|id_utente|standardized                                              |
+---------+----------------------------------------------------------+
|CA_11666 |[3.8148588642668853,1.317585214797919,0.43758486029695165]|
|CA_11978 |[1.6690007531167623,0.6953921966989017,0.0]               |
|CA_12200 |[1.621315017313426,0.0,0.0]                               |
|CA_12787 |[2.956515619806836,1.8909787804970135,0.8751697205939033] |
|CA_13151 |[1.2875148666900738,0.8417905538986704,0.0]               |
|CA_13170 |[2.193543846953459,0.0,0.0]                               |
|CA_1410  |[1.7166864889200983,2.940167007095356,2.62550916178171]   |
|CA_14350 |[2.6704012049868195,0.9149897324985549,0.0]               |
|CA_14628 |[1.621315017313426,0.6221930180990173,0.0]                |
|CA_1477  |[3.9579160716768933,2.549771387895973,1.312754580890855]  |
+---------+----------------------------------------------------------+
only s

##### Clustering (K-Means with Elbow Method)

In [17]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator
import matplotlib.pyplot as plt

silhouette_score = []
evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='standardized', \
                                metricName='silhouette', distanceMeasure='squaredEuclidean')
# for i in range(2, 5):
#     # K-Mean Clustering with "i" centers
#     output  = KMeans(featuresCol = 'standardized', k = i).fit(df_kmeans).transform(df_kmeans)
#     # Computing the silhouette score
#     score   = evaluator.evaluate(output)
#     silhouette_score.append(score)
#     print("Silhouette Score: ", score)
    
# K-Mean Clustering with "i" centers
output  = KMeans(featuresCol = 'standardized', k = 2).fit(df_kmeans).transform(df_kmeans)
# Computing the silhouette score
score   = evaluator.evaluate(output)
silhouette_score.append(score)
print("Silhouette Score: ", score) 

print(output)    
#Visualizing the silhouette scores in a plot
# fig, ax = plt.subplots(1, 1, figsize =(8,6))
# ax.plot(range(2,10), silhouette_score)
# ax.set_xlabel('k')
# ax.set_ylabel('silhouette')

Silhouette Score:  0.5961054301569151
DataFrame[id_utente: string, standardized: vector, prediction: int]


In [19]:
output.show(1)

DataFrame[id_utente: string, standardized: vector, prediction: int]

In [ ]:
### TODO: Salvare su filesystem locale le predizioni 

##### TODO: Scatter plot with cluster colors...

In [49]:
import matplotlib as plt
%matplotlib widget
sample_pandas_df['prediction'] = output.toPandas()['prediction']
sample_pandas_df.plot(kind = 'scatter', x = 'TOT_tk_guadagnati', y = 'TOT_tk_spesi', c = 'prediction', colormap='viridis' )
# def scatter_plot(x, y):
#     # create a new plot with a title and axis labels
#     p = figure(title="Scatter Plot", x_axis_label=x, y_axis_label=y)
#     p.circle(sample_pandas_df[x], sample_pandas_df[y], legend_label="Objects", line_color="yellow", size=5, alpha=0.3)
#     p.add_tools(BoxSelectTool(dimensions="width"), BoxSelectTool(dimensions="height"), CrosshairTool(),
#         HoverTool(tooltips=[
#             ( x, '@x' ), # use @{ } for field names with spaces
#             ( y, '@y' ),
#         ]))
#     show(p)

# scatter = interact(scatter_plot,
#                           x=[item[0] for item in final_data.dtypes if item[1] not in ('string')], # select only the "no string" columns with a List comprehension \
#                           y=[item[0] for item in final_data.dtypes if item[1] not in ('string')][1:])

# scatter.widget.children[2].description = "Scatter Plot Data"
# scatter.widget.children[2].button_style = "success"

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

<AxesSubplot:xlabel='TOT_tk_guadagnati', ylabel='TOT_tk_spesi'>

### Release the resource (delete executor Pods)

In [18]:
def stopSpark():
    global spark
    global sc
    spark.stop()
    sc.stop()

stopper = interact_manual(stopSpark)
stopper.widget.children[0].description = "Stop Spark"
stopper.widget.children[0].button_style = "danger"


interactive(children=(Button(description='Run Interact', style=ButtonStyle()), Output()), _dom_classes=('widge…